In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from collections import Counter
from sklearn.ensemble import RandomForestRegressor
from sklearn import metrics

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session


In [31]:
test_data = pd.read_csv('hotels_test.csv')
train_data = pd.read_csv('hotels_train.csv')
# для корректной обработки признаков объединяем трейн и тест в один датасет
train_data['sample'] = 1 # помечаем train
test_data['sample'] = 0 # помечаем test
test_data['reviewer_score'] = 0 
# в test у нас нет значения reviewer_score, мы его должны предсказать, по этому заполняем нулями

data = test_data.append(train_data, sort=False).reset_index(drop=True)

C:\Users\79262\AppData\Local\Temp\ipykernel_4112\3631439687.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = test_data.append(train_data, sort=False).reset_index(drop=True)


In [10]:
print(data.shape)
data.tail(3)

(515738, 18)


hotel_address  \
515735  29 31 Gower Street Camden London WC1E 6HG Unit...   
515736  31 Great Cumberland Place Westminster Borough ...   
515737  25 Courtfield Gardens Kensington and Chelsea L...   

        additional_number_of_scoring review_date  average_score  \
515735                           457    2/7/2016            6.8   
515736                           365   5/21/2017            8.1   
515737                           222    8/5/2016            9.0   

                     hotel_name    reviewer_nationality  \
515735  Bloomsbury Palace Hotel            Netherlands    
515736   The Marble Arch London   United Arab Emirates    
515737    The Nadler Kensington              Australia    

                                          negative_review  \
515735   room is really small but guess is normal in L...   
515736                                        No Negative   
515737   Patio outside could have been cleaned of alga...   

        review_total_negative_word_counts  total_number_of_reviews  \
515735                                 12                     2751   
515736                                  0                     1567   
515737                                 20                     1209   

                                          positive_review  \
515735     great location simple check in out nice shower   
515736                        Location and very comfy bed   
515737   Beds comfortable Pillows also good Homely fee...   

        review_total_positive_word_counts  \
515735                                  9   
515736                                  6   
515737                                 20   

        total_number_of_reviews_reviewer_has_given  \
515735                                          21   
515736                                          28   
515737                                           2   

                                                     tags days_since_review  \
515735  [' Business trip ', ' Solo traveler ', ' Singl...           543 day   
515736  [' Leisure trip ', ' Solo traveler ', ' Deluxe...           74 days   
515737  [' Leisure trip ', ' Couple ', ' Bunk Bed Room...           363 day   

              lat       lng  sample  reviewer_score  
515735  51.520795 -0.131084       1             8.3  
515736  51.515125 -0.160066       1             9.2  
515737  51.493109 -0.190208       1             8.8

In [ ]:
#pip install pandas-profilingb

In [12]:
import pandas as pd
from pandas_profiling import ProfileReport
profile = ProfileReport(data, title="Booking Pandas Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Первоначальная версия датасета содержит 17 полей со следующей информацией:

- hotel_address — адрес отеля;
- review_date — дата, когда рецензент разместил соответствующий отзыв;
- average_score — средний балл отеля, рассчитанный на основе последнего комментария за последний год;
- hotel_name — название отеля;
- reviewer_nationality — страна рецензента;
- negative_review — отрицательный отзыв, который рецензент дал отелю;
- review_total_negative_word_counts — общее количество слов в отрицательном отзыв;
- positive_review — положительный отзыв, который рецензент дал отелю;
- review_total_positive_word_counts — общее количество слов в положительном отзыве.
- reviewer_score — оценка, которую рецензент поставил отелю на основе своего опыта;
- total_number_of_reviews_reviewer_has_given — количество отзывов, которые рецензенты дали в прошлом;
- total_number_of_reviews — общее количество действительных отзывов об отеле;
- tags — теги, которые рецензент дал отелю;
- days_since_review — количество дней между датой проверки и датой очистки;
- additional_number_of_scoring — есть также некоторые гости, которые просто поставили оценку сервису, но не оставили отзыв. Это число указывает, сколько там действительных оценок без проверки.
- lat — географическая широта отеля;
- lng — географическая долгота отеля.

In [15]:
#data['duplicat'] = data.duplicated()
def dupl(arg):
    if False in arg:
        return 0
    else:
        return 1
data['duplicated'] = data['duplicat'].apply(dupl)
#data = data.drop('duplicat', axis=1)

data.head()


TypeError: argument of type 'bool' is not iterable

In [14]:
data.head()

hotel_address  \
0                 Via Senigallia 6 20161 Milan Italy   
1  Arlandaweg 10 Westpoort 1043 EW Amsterdam Neth...   
2        Mallorca 251 Eixample 08008 Barcelona Spain   
3  Piazza Della Repubblica 17 Central Station 201...   
4  Singel 303 309 Amsterdam City Center 1012 WJ A...   

   additional_number_of_scoring review_date  average_score  \
0                           904   7/21/2017            8.1   
1                           612  12/12/2016            8.6   
2                            46  11/26/2015            8.3   
3                           241  10/17/2015            9.1   
4                           834   5/16/2016            9.1   

                                   hotel_name        reviewer_nationality  \
0                              Hotel Da Vinci             United Kingdom    
1                           Urban Lodge Hotel                    Belgium    
2  Alexandra Barcelona A DoubleTree by Hilton                     Sweden    
3                    Hotel Principe Di Savoia   United States of America    
4                              Hotel Esther a             United Kingdom    

                                     negative_review  \
0   Would have appreciated a shop in the hotel th...   
1        No tissue paper box was present at the room   
2                                           Pillows    
3                                        No Negative   
4                                        No Negative   

   review_total_negative_word_counts  total_number_of_reviews  \
0                                 52                    16670   
1                                 10                     5018   
2                                  3                      351   
3                                  0                     1543   
4                                  0                     4687   

                                     positive_review  \
0   Hotel was great clean friendly staff free bre...   
1                                        No Positive   
2                         Nice welcoming and service   
3   Everything including the nice upgrade The Hot...   
4                    Lovely hotel v welcoming staff    

   review_total_positive_word_counts  \
0                                 62   
1                                  0   
2                                  5   
3                                 27   
4                                  7   

   total_number_of_reviews_reviewer_has_given  \
0                                           1   
1                                           7   
2                                          15   
3                                           9   
4                                           2   

                                                tags days_since_review  \
0  [' Leisure trip ', ' Couple ', ' Double Room '...           13 days   
1  [' Leisure trip ', ' Group ', ' Triple Room ',...           234 day   
2  [' Business trip ', ' Solo traveler ', ' Twin ...           616 day   
3  [' Leisure trip ', ' Couple ', ' Ambassador Ju...           656 day   
4  [' Business trip ', ' Solo traveler ', ' Class...           444 day   

         lat       lng  sample  reviewer_score  duplicat  
0  45.533137  9.171102       0             0.0     False  
1  52.385649  4.834443       0             0.0     False  
2  41.393192  2.161520       0             0.0     False  
3  45.479888  9.196298       0             0.0     False  
4  52.370545  4.888644       0             0.0     False

In [ ]:
# Задание 4.4 Сколько уникальных тегов представлено в наборе данных?
#def re_func(num_tags):
#    found = re.findall("'[^\'](.+?)[^\']'", num_tags) # re - нужен импорт регулярного...
#    return found
#print(hotels['tags'].apply(re_func).explode().nunique())
# 2368

In [ ]:
# способ решения задания 4.4.
tags = list() # множество тегов
for i, row in hotels['tags'].items():
    tmp = row.replace("[' ", "")
    tmp = tmp.replace(" ']", '')
    tmp = tmp.split(" ', ' ")
    for el in tmp:
        if el not in tags:
            tags.append(el)
print(f'Уникальных тегов = {len(tags)}')

In [ ]:
# Задание 4.5 Какой тег представлен в наибольшем числе отзывов?
from collections import Counter

cnt = Counter() 
for i, row in hotels['tags'].items():
    tmp = row.replace("[' ", "")
    tmp = tmp.replace(" ']", '')
    tmp = tmp.split(" ', ' ")
    cnt.update(tmp)
print(cnt.most_common(1))

#или так
for key, values in cnt.most_common(1): 
    print(key)

In [ ]:
cnt_data = pd.Series(cnt)
((cnt_data.sort_values(ascending=False)).head())

### object:
- hotel_address
- review_date
- hotel_name
- reviewer_nationality 
- negative_review
- positive_review
- tags
- days_since_review

In [ ]:
 # убираем признаки которые еще не успели обработать, !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
 # модель на признаках с dtypes "object" обучаться не будет, просто выберим их и удалим
 object_columns = [s for s in hotels.columns if hotels[s].dtypes == 'object']
 hotels.drop(object_columns, axis = 1, inplace=True)

 # заполняем пропуски самым простым способом!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
 hotels = hotels.fillna(0)

In [ ]:
# Разбиваем датафрейм на части, необходимые для обучения и тестирования модели  
# Х - данные с информацией об отелях, у - целевая переменная (рейтинги отелей)  
X = hotels.drop(['reviewer_score'], axis = 1)  
y = hotels['reviewer_score'] 

In [ ]:
# Загружаем специальный инструмент для разбивки:  
from sklearn.model_selection import train_test_split  

In [ ]:
# Наборы данных с меткой "train" будут использоваться для обучения модели, "test" - для тестирования.  
# Для тестирования мы будем использовать 25% от исходного датасета.  
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=42)

In [ ]:
# Импортируем необходимые библиотеки:  
from sklearn.ensemble import RandomForestRegressor # инструмент для создания и обучения модели  
from sklearn import metrics # инструменты для оценки точности модели  
  
# Создаём модель  
regr = RandomForestRegressor(n_estimators=100)  
      
# Обучаем модель на тестовом наборе данных  
regr.fit(X_train, y_train)  
      
# Используем обученную модель для предсказания рейтинга отелей в тестовой выборке.  
# Предсказанные значения записываем в переменную y_pred  
y_pred = regr.predict(X_test)  


In [ ]:
# Сравниваем предсказанные значения (y_pred) с реальными (y_test), и смотрим насколько они отличаются  
# Метрика называется Mean Absolute Percentage Error (MAPE) и показывает среднюю абсолютную процентную ошибку предсказанных значений от фактических.  
print('MAPE:', metrics.mean_absolute_percentage_error(y_test, y_pred))

Небольшой бонус:


In [25]:
#from multiprocessing.reduction import duplicate


data['duplicat'].describe()

count     515738
unique         2
top        False
freq      515402
Name: duplicat, dtype: object

In [30]:
sorted = data.sort_values(by='duplicat')
sorted.tail()

hotel_address  \
514376  40 Rue du Commandant Ren Mouchotte 14th arr 75...   
423537  40 Rue du Commandant Ren Mouchotte 14th arr 75...   
335184  40 Rue du Commandant Ren Mouchotte 14th arr 75...   
505307  40 Rue du Commandant Ren Mouchotte 14th arr 75...   
429457      9 Rue Sainte Beuve 6th arr 75006 Paris France   

        additional_number_of_scoring review_date  average_score  \
514376                           228   8/25/2015            7.9   
423537                           228   8/18/2015            7.9   
335184                           228    3/1/2016            7.9   
505307                           228   10/1/2015            7.9   
429457                            22    4/6/2017            8.9   

                         hotel_name reviewer_nationality  \
514376  H tel Concorde Montparnasse              France    
423537  H tel Concorde Montparnasse      United Kingdom    
335184  H tel Concorde Montparnasse              Turkey    
505307  H tel Concorde Montparnasse      United Kingdom    
429457        Hotel Le Sainte Beuve      United Kingdom    

                                          negative_review  \
514376   Rooms not very noise insulated within the bui...   
423537   Very poor service wifi almost none exists bre...   
335184                  Small room size limited sunlight    
505307                              No kettle in our room   
429457   I asked if i could have a coffee the morning ...   

        review_total_negative_word_counts  total_number_of_reviews  \
514376                                  9                     2515   
423537                                 14                     2515   
335184                                  7                     2515   
505307                                  6                     2515   
429457                                 47                      143   

                          positive_review  review_total_positive_word_counts  \
514376                        No Positive                                  0   
423537               Location is not bad                                   6   
335184   Perfect location Friendly staff                                   6   
505307                       The location                                  3   
429457                        No Positive                                  0   

        total_number_of_reviews_reviewer_has_given  \
514376                                          18   
423537                                           2   
335184                                           4   
505307                                           1   
429457                                          10   

                                                     tags days_since_review  \
514376  [' Leisure trip ', ' Couple ', ' Superior Doub...           709 day   
423537  [' Leisure trip ', ' Group ', ' Classic Twin R...           716 day   
335184  [' Leisure trip ', ' Couple ', ' Classic Doubl...           520 day   
505307  [' Leisure trip ', ' Couple ', ' Superior Doub...           672 day   
429457  [' Leisure trip ', ' Couple ', ' Superior Room...           119 day   

              lat       lng  sample  reviewer_score  duplicat  
514376  48.838108  2.318669       1             8.3      True  
423537  48.838108  2.318669       1             3.3      True  
335184  48.838108  2.318669       1             8.8      True  
505307  48.838108  2.318669       1             7.0      True  
429457  48.843900  2.329486       1             5.0      True

In [ ]:
# непрерывные признаки
num_cols = ['total_number_of_reviews', 'review_total_negative_word_counts', ...]

# категориальные признаки
cat_cols = ['average_score', 'lat', ...]